# Information from e-mail

The second exercise focuses on alignment. A single root file is provided, called Alignment.root. Inside this root file you will find 7 ttrees. The first two ttrees, preparation1 and preparation2, are relatively simple and just show how data can be stored in a ttree. The preparation2 one is particularly important because it is showing how an array of values can be stored for each event. The next 4 ttrees (step1 to step4) are the bulk of the exercise. The last ttree, challenge, is a challenge if you would like to try it. Each of these ttree has the emulated data from 6 pixel detectors. The detectors are placed along the z axis at positions 10 cm, 20 cm, 45 cm, 70 cm, 78 cm, 84 cm. Each event stored in the ttree corresponds to one particle travelling through the detectors. The trees have the following properties:
  - step1: the detectors are perfectly aligned, this is provided for you to experiment and test things out
  - step2: the detectors are misaligned by unknown amounts in the x axis. You have to figure out by how much for each detector
  - step3: the detectors are misaligned by unknown amounts in the y axis. You have to figure out by how much for each detector
  - step4: the detectors are misaligned by unknown amounts in the x and y axis. You have to figure out by how much for each detector
  - challenge: you have no information on the detectors apart from the position along z. Can you figure out the alignment of the detectors?
  
In all trees of this exercise the pixel6 detector has its position perfectly known, centered at (0, 0, 84). You will need to calculate the alignment for the other detectors. The simulated pixel detectors have dimensions of 4 cm by 2 cm with 1200 pixels in x and 600 in y, making a total of 720k pixels. When a particle traverses a pixel detector it deposits some energy locally, this energy is spread over an area and typically affects more than one pixel. Each pixel that passes a threshold is said to be a hit. You will notice in the ttree that there are branches called pixelN_numHits, this is the number of hits in that detector for that event. The pixelN_hitX and pixelN_hitY are the coordinates in X and Y of the corresponding pixel hits (i.e. these branches are actually arrays of values per event). Finally, you will see another two branches pixelN_clusterX and pixelN_clusterY, these are the result of running a clustering algorithm on the hits and are the output of a would-be reconstruction code. A good mini exercise could be for you to take the hits themselves and try to get yourselves the cluster X and Y values.

In [1]:
from ROOT import TFile

inputFile = TFile("Alignment.root", "READ")

Welcome to JupyROOT 6.18/02


In [2]:
inputFile.ls()

TFile**		Alignment.root	
 TFile*		Alignment.root	
  KEY: TTree	preparation1;1	simple tree
  KEY: TTree	preparation2;1	a tree with an array
  KEY: TTree	step1;1	6 Pixel detectors aligned
  KEY: TTree	step2;1	6 Pixel detectors with unknown shifts in x
  KEY: TTree	step3;1	6 Pixel detectors with unknown shifts in y
  KEY: TTree	step4;1	6 Pixel detectors with unknown shifts in x and y
  KEY: TTree	challenge;1	6 Pixel detectors: are you able to figure out what happened to these detectors?


In [3]:
preparation2 = inputFile.Get("preparation2")

preparation2.Print()

******************************************************************************
*Tree    :preparation2: a tree with an array                                   *
*Entries :       25 : Total =            3630 bytes  File  Size =       1673 *
*        :          : Tree compression factor =   1.67                       *
******************************************************************************
*Br    0 :n         : Int_t A simple branch of type int                      *
*Entries :       25 : Total  Size=        669 bytes  File Size  =        136 *
*Baskets :        1 : Basket Size=      32000 bytes  Compression=   1.29     *
*............................................................................*
*Br    1 :M         : Float_t A simple branch of type float                  *
*Entries :       25 : Total  Size=        671 bytes  File Size  =        176 *
*Baskets :        1 : Basket Size=      32000 bytes  Compression=   1.00     *
*.................................................

In [4]:
for event in preparation2:
    print("This event has", event.n, "entries")
    for i in range(event.n):
        print("  Entry", i, ":", event.array[i])

This event has 0 entries
This event has 1 entries
  Entry 0 : 0.10000000149011612
This event has 2 entries
  Entry 0 : 0.20000000298023224
  Entry 1 : 1.2000000476837158
This event has 3 entries
  Entry 0 : 0.30000001192092896
  Entry 1 : 1.2999999523162842
  Entry 2 : 2.299999952316284
This event has 4 entries
  Entry 0 : 0.4000000059604645
  Entry 1 : 1.399999976158142
  Entry 2 : 2.4000000953674316
  Entry 3 : 3.4000000953674316
This event has 5 entries
  Entry 0 : 0.5
  Entry 1 : 1.5
  Entry 2 : 2.5
  Entry 3 : 3.5
  Entry 4 : 4.5
This event has 6 entries
  Entry 0 : 0.6000000238418579
  Entry 1 : 1.600000023841858
  Entry 2 : 2.5999999046325684
  Entry 3 : 3.5999999046325684
  Entry 4 : 4.599999904632568
  Entry 5 : 5.599999904632568
This event has 7 entries
  Entry 0 : 0.699999988079071
  Entry 1 : 1.7000000476837158
  Entry 2 : 2.700000047683716
  Entry 3 : 3.700000047683716
  Entry 4 : 4.699999809265137
  Entry 5 : 5.699999809265137
  Entry 6 : 6.699999809265137
This event has 

Now that we understand how arrays work inside flat TTrees, lets take a look at the data from the pixels

In [5]:
from ROOT import TCanvas

step1 = inputFile.Get("step1")
step1.Print()

******************************************************************************
*Tree    :step1     : 6 Pixel detectors aligned                              *
*Entries :     5000 : Total =         1941435 bytes  File  Size =     688635 *
*        :          : Tree compression factor =   2.81                       *
******************************************************************************
*Br    0 :pixel0_numHits : Int_t Number of hits in pixel detector 0          *
*Entries :     5000 : Total  Size=      20621 bytes  File Size  =       3047 *
*Baskets :        1 : Basket Size=      32000 bytes  Compression=   6.59     *
*............................................................................*
*Br    1 :pixel0_hitX : Int_t Hit x positions on pixel detector 0            *
*Entries :     5000 : Total  Size=     133114 bytes  File Size  =      42425 *
*Baskets :        5 : Basket Size=      32000 bytes  Compression=   3.12     *
*...................................................

In [7]:
counter = 0
myArray = []
for event in step1:
    print("Event", counter, "has", event.pixel0_numHits, "hits")
    for idx in range(event.pixel0_numHits):
        print("  Hit", idx, ": X =", event.pixel0_hitX[idx], " Y =", event.pixel0_hitY[idx])
    print("  Cluster X =", event.pixel0_clusterX, " Y =", event.pixel0_clusterY)
    counter += 1
    myArray += [event.pixel0_clusterX]
    if counter == 5:
        break
        
print(myArray)

Event 0 has 0 hits
  Cluster X = 0.0  Y = 0.0
Event 1 has 7 hits
  Hit 0 : X = 545  Y = 195
  Hit 1 : X = 545  Y = 196
  Hit 2 : X = 546  Y = 195
  Hit 3 : X = 546  Y = 196
  Hit 4 : X = 546  Y = 197
  Hit 5 : X = 547  Y = 195
  Hit 6 : X = 547  Y = 196
  Cluster X = -0.1783333271741867  Y = -0.3459523916244507
Event 2 has 6 hits
  Hit 0 : X = 885  Y = 336
  Hit 1 : X = 885  Y = 337
  Hit 2 : X = 886  Y = 336
  Hit 3 : X = 886  Y = 337
  Hit 4 : X = 887  Y = 336
  Hit 5 : X = 887  Y = 337
  Cluster X = 0.9549999833106995  Y = 0.12333333492279053
Event 3 has 7 hits
  Hit 0 : X = 500  Y = 359
  Hit 1 : X = 501  Y = 358
  Hit 2 : X = 501  Y = 359
  Hit 3 : X = 501  Y = 360
  Hit 4 : X = 502  Y = 358
  Hit 5 : X = 502  Y = 359
  Hit 6 : X = 502  Y = 360
  Cluster X = -0.3273809552192688  Y = 0.19833333790302277
Event 4 has 7 hits
  Hit 0 : X = 547  Y = 322
  Hit 1 : X = 547  Y = 323
  Hit 2 : X = 548  Y = 322
  Hit 3 : X = 548  Y = 323
  Hit 4 : X = 548  Y = 324
  Hit 5 : X = 549  Y = 322


In [ ]:
c1 = TCanvas("c1", "c1", 800, 600)
step1.Draw("pixel0_clusterX:pixel1_clusterX")
c1.Draw()

In [ ]:
c2 = TCanvas("c2", "c2", 800, 600)
step1.Draw("pixel0_clusterX:pixel1_clusterX", "pixel0_numHits>0 && pixel1_numHits>0")
c2.Draw()

In [ ]:
step2 = inputFile.Get("step2")
c3 = TCanvas("c3", "c3", 800, 600)
step2.Draw("pixel0_clusterX:pixel1_clusterX", "pixel0_numHits>0 && pixel1_numHits>0")
c3.Draw()

In [ ]:
challenge = inputFile.Get("challenge")
c4 = TCanvas("c4", "c4", 800, 600)
challenge.Draw("pixel0_clusterX:pixel5_clusterX", "pixel0_numHits>0 && pixel5_numHits>0")
c4.Draw()